
### Calling common notebook to re-use variables

In [0]:
%run "/Workspace/Users/khanhminh12723_gmail.com#ext#@khanhminh12723gmail.onmicrosoft.com/04. Common notebook"

# To re-use common functions and variables


# Re-Using functions
- We can re-use 2 functions here
  - Removing Duplicates
  - Removing NULLs

# Defining all common variables

## Defining common functions

### 01 -- Removing duplicates

### 01 -- Handling NULLs

In [0]:
dbutils.widgets.text(name="env",defaultValue='',label='Enter the environment in lower case')
env = dbutils.widgets.get("env")


### Read Silver_Traffic table

In [0]:
def read_SilverTrafficTable(environment):
    print('Reading the Silver Traffic Table Data : ',end='')
    df_SilverTraffic = (spark.readStream
                    .table(f"`{environment}`.`silver`.silver_traffic")
                    )
    print(f'Reading {environment}.silver.silver_traffic Success!')
    print("**********************************")
    return df_SilverTraffic


### Read silver_roads Table

In [0]:

def read_SilverRoadsTable(environment):
    print('Reading the Silver Table Silver_roads Data : ',end='')
    df_SilverRoads = (spark.readStream
                    .table(f"`{environment}`.`silver`.silver_roads")
                    )
    print(f'Reading {environment}.silver.silver_roads Success!')
    print("**********************************")
    return df_SilverRoads


## Creating vehicle Intensity Column

In [0]:
def create_VehicleIntensity(df):
 from pyspark.sql.functions import col
 print('Creating Vehicle Intensity column : ',end='')
 df_veh = df.withColumn('Vehicle_Intensity',
               col('Motor_Vehicles_Count') / col('Link_length_km')
               )
 print("Success!!!")
 print('***************')
 return df_veh

### Creating LoadTime column

In [0]:
def create_LoadTime(df):
    from pyspark.sql.functions import current_timestamp
    print('Creating Load Time column : ',end='')
    df_timestamp = df.withColumn('Load_Time',
                      current_timestamp()
                      )
    print('Success!!')
    print('**************')
    return df_timestamp


### Writing Data to Gold Traffic

In [0]:
def write_Traffic_GoldTable(StreamingDF,environment):
    print('Writing the gold_traffic Data : ',end='') 

    write_gold_traffic = (StreamingDF.writeStream
                .format('delta')
                .option('checkpointLocation',checkpoint+ "GoldTrafficLoad/Checkpt/")
                .outputMode('append')
                .queryName("GoldTrafficWriteStream")
                .trigger(availableNow=True)
                .toTable(f"`{environment}`.`gold`.`gold_traffic`"))
    
    write_gold_traffic.awaitTermination()
    print(f'Writing `{environment}`.`gold`.`gold_traffic` Success!')


### Writing Data to Gold Roads

In [0]:
def write_Roads_GoldTable(StreamingDF,environment):
    print('Writing the gold_roads Data : ',end='') 

    write_gold_roads = (StreamingDF.writeStream
                .format('delta')
                .option('checkpointLocation',checkpoint+ "GoldRoadsLoad/Checkpt/")
                .outputMode('append')
                .queryName("GoldRoadsWriteStream")
                .trigger(availableNow=True)
                .toTable(f"`{environment}`.`gold`.`gold_roads`"))
    
    write_gold_roads.awaitTermination()
    print(f'Writing `{environment}`.`gold`.`gold_roads` Success!')


## Calling all functions

In [0]:
## Reading from Silver tables
df_SilverTraffic = read_SilverTrafficTable(env)
df_SilverRoads = read_SilverRoadsTable(env)
    
## Tranformations     
df_vehicle = create_VehicleIntensity(df_SilverTraffic)
df_FinalTraffic = create_LoadTime(df_vehicle)
df_FinalRoads = create_LoadTime(df_SilverRoads)


## Writing to gold tables    
write_Traffic_GoldTable(df_FinalTraffic,env)
write_Roads_GoldTable(df_FinalRoads,env)

Reading the Silver Traffic Table Data : Reading databricks_dev_wp.silver.silver_traffic Success!
**********************************
Reading the Silver Table Silver_roads Data : Reading databricks_dev_wp.silver.silver_roads Success!
**********************************
Creating Vehicle Intensity column : Success!!!
***************
Creating Load Time column : Success!!
**************
Creating Load Time column : Success!!
**************
Writing the gold_traffic Data : Writing `databricks_dev_wp`.`gold`.`gold_traffic` Success!
Writing the gold_roads Data : Writing `databricks_dev_wp`.`gold`.`gold_roads` Success!


In [0]:
%sql

SELECT * FROM `databricks_dev_wp`.`gold`.`gold_traffic`

Record_ID Count_point_id Direction_of_travel Year Count_date hour Region_id Region_name Local_authority_name Road_name Road_Category_ID Start_junction_road_name End_junction_road_name Latitude Longitude Link_length_km Pedal_cycles Two_wheeled_motor_vehicles Cars_and_taxis Buses_and_coaches LGV_Type HGV_Type EV_Car EV_Bike Extract_Time Electric_Vehicles_Count Motor_Vehicles_Count Transformed_Time Vehicle_Intensity Load_Time 18555 46818 N 2014 9/11/2014 0:00 13 6 London Croydon A222 4 A232 A222 Lower Addiscombe Rd 51.37750343 -0.091631091 1.1 3 1 176 21 19 5 1 4 2025-09-19T16:58:10.287Z 5 227 2025-09-20T10:47:42.789Z 206.36363636363635 2025-09-20T16:22:53.005Z 18582 37072 N 2014 10/24/2014 0:00 16 1 South West Devon A380 4 A381 A381/A383 50.53694661 -3.587025595 2.5 0 19 1106 6 220 24 5 0 2025-09-19T16:58:10.287Z 5 1380 2025-09-20T10:47:42.789Z 552.0 2025-09-20T16:22:53.005Z 18697 40810 S 2014 6/25/2014 0:00 18 3 Scotland Glasgow City M8 1 18 17 55.86617849 -4.271505582 1.1 0 9 3248 14 364 28 5 4 2025-09-19T16:58:10.287Z 9 3672 2025-09-20T10:47:42.789Z 3338.181818181818 2025-09-20T16:22:53.005Z 19325 16262 E 2014 6/26/2014 0:00 9 9 South East Kent A25 4 A21(T) B2042 51.27949102 0.156455883 1.0 1 4 498 3 83 30 0 10 2025-09-19T16:58:10.287Z 10 628 2025-09-20T10:47:42.789Z 628.0 2025-09-20T16:22:53.005Z 19498 38071 S 2014 9/2/2014 0:00 14 10 West Midlands Walsall M6 1 10 LA Boundary 52.60408534 -2.019152202 3.7 0 13 2735 7 762 331 60 40 2025-09-19T16:58:10.287Z 100 3948 2025-09-20T10:47:42.789Z 1067.027027027027 2025-09-20T16:22:53.005Z 19549 17809 N 2014 9/5/2014 0:00 12 8 Yorkshire and the Humber Sheffield A61 4 A57 Brook Hill A61 Shalesmoor 53.38770253 -1.478229817 0.9 1 14 868 14 142 43 6 7 2025-09-19T16:58:10.287Z 13 1094 2025-09-20T10:47:42.789Z 1215.5555555555554 2025-09-20T16:22:53.005Z 19726 16119 E 2014 6/19/2014 0:00 15 1 South West Wiltshire A4 4 A435 A436 51.41971027 -1.732466102 0.7 3 0 532 15 86 9 0 1 2025-09-19T16:58:10.287Z 1 643 2025-09-20T10:47:42.789Z 918.5714285714287 2025-09-20T16:22:53.005Z 19808 46034 E 2014 7/4/2014 0:00 15 9 South East Kent M20 1 6 7 51.29092541 0.537087844 2.9 0 36 3385 24 864 84 12 33 2025-09-19T16:58:10.287Z 45 4438 2025-09-20T10:47:42.789Z 1530.344827586207 2025-09-20T16:22:53.005Z 20101 17297 N 2014 7/4/2014 0:00 8 2 East Midlands Nottingham A610 4 A6514 A6130 52.96625149 -1.18255712 1.1 9 2 752 39 157 11 3 8 2025-09-19T16:58:10.287Z 11 972 2025-09-20T10:47:42.789Z 883.6363636363635 2025-09-20T16:22:53.005Z 20193 26121 E 2014 5/19/2014 0:00 16 9 South East Reading A4 4 Burghfield Rd Honey End Lane 51.44449111 -1.017193502 0.3 11 6 548 9 95 5 4 3 2025-09-19T16:58:10.287Z 7 670 2025-09-20T10:47:42.789Z 2233.3333333333335 2025-09-20T16:22:53.005Z 20228 17538 E 2014 5/19/2014 0:00 7 1 South West Plymouth A386 4 Beauchamp rd A38 50.39795375 -4.140063284 1.1 25 26 1472 30 277 11 0 0 2025-09-19T16:58:10.287Z 0 1816 2025-09-20T10:47:42.789Z 1650.9090909090908 2025-09-20T16:22:53.005Z 20309 27530 S 2014 9/15/2014 0:00 16 7 East of England Hertfordshire A1072 4 A1070 A1155 51.90118645 -0.214368167 0.7 7 9 574 13 114 12 0 2 2025-09-19T16:58:10.287Z 2 724 2025-09-20T10:47:42.789Z 1034.2857142857144 2025-09-20T16:22:53.005Z 21253 37061 S 2014 4/23/2014 0:00 17 1 South West Devon A375 4 C Seaton Road A35 50.79336598 -3.202101826 4.5 1 5 271 2 29 0 0 0 2025-09-19T16:58:10.287Z 0 307 2025-09-20T10:47:42.789Z 68.22222222222223 2025-09-20T16:22:53.005Z 22478 46515 W 2014 5/21/2014 0:00 9 7 East of England Norfolk A47 3 A148 A10/A149 52.73599731 0.398430801 1.6 0 3 610 4 150 32 16 5 2025-09-19T16:58:10.287Z 21 820 2025-09-20T10:47:42.789Z 512.5 2025-09-20T16:22:53.005Z 22571 38059 N 2014 9/22/2014 0:00 12 5 North West Lancashire M65 2 11 12 53.81102152 -2.253228371 4.2 0 6 1438 3 288 29 6 11 2025-09-19T16:58:10.287Z 17 1781 2025-09-20T10:47:42.789Z 424.04761904761904 2025-09-20T16:22:53.005Z 22621 46690 W 2014 7/4/2014 0:00 14 7 East of England Essex A1060 4 A1098 A1060 51.72881217 0.478268513 0.5 9 17 

In [0]:
%sql
SELECT * FROM `databricks_dev_wp`.`gold`.`gold_roads`

Road_ID Road_Category_Id Road_Category Region_ID Region_Name Total_Link_Length_Km Total_Link_Length_Miles All_Motor_Vehicles Road_Category_Name Road_Type Load_Time 23 3 TA 6 London 339.479 210.94 3.913260559E9 Class A Trunk Road Major 2025-09-20T16:23:09.205Z 39 5 M 9 South East 40851.1 25383.7 1.5597621429E10 Class B road Minor 2025-09-20T16:23:09.205Z 31 2 PM 8 Yorkshire and the Humber 5.612 3.49 7.880772228E7 Class A Principal Motorway Major 2025-09-20T16:23:09.205Z 13 1 TM 4 Wales 130.291 80.96 1.306589845E9 Class A Trunk Motor Major 2025-09-20T16:23:09.205Z 65 5 M 4 Wales 28370.8 17628.8 5.374885013E9 Class B road Minor 2025-09-20T16:23:09.205Z 67 2 PM 5 North West 38.642 24.01 3.055495587E8 Class A Principal Motorway Major 2025-09-20T16:23:09.205Z 12 5 M 3 Scotland 47971.6 29808.17 7.656438848E9 Class B road Minor 2025-09-20T16:23:09.205Z 52 4 PA 1 South West 3882.154 2412.26 8.028746829E9 Class A Principal road Major 2025-09-20T16:23:09.205Z 29 5 M 7 East of England 34610.8 21506.15 1.1083436184E10 Class B road Minor 2025-09-20T16:23:09.205Z 53 5 M 1 South West 43659.6 27128.82 9.272591264E9 Class B road Minor 2025-09-20T16:23:09.205Z 60 4 PA 3 Scotland 7419.724 4610.4 6.67873035E9 Class A Principal road Major 2025-09-20T16:23:09.205Z 36 2 PM 9 South East 16.997 10.56 2.167368363E8 Class A Principal Motorway Major 2025-09-20T16:23:09.205Z 51 3 TA 1 South West 991.224 615.92 3.592467081E9 Class A Trunk Road Major 2025-09-20T16:23:09.205Z 44 5 M 10 West Midlands 27956.1 17371.12 9.927697665E9 Class B road Minor 2025-09-20T16:23:09.205Z 45 1 TM 11 North East 51.268 31.86 4.734966048E8 Class A Trunk Motor Major 2025-09-20T16:23:09.205Z 27 3 TA 7 East of England 1134.757 705.11 5.738079521E9 Class A Trunk Road Major 2025-09-20T16:23:09.205Z 69 4 PA 5 North West 3133.096 1946.82 8.658580954E9 Class A Principal road Major 2025-09-20T16:23:09.205Z 3 4 PA 1 South West 3874.924 2407.77 7.794003682E9 Class A Principal road Major 2025-09-20T16:23:09.205Z 72 3 TA 6 London 335.84 208.68 3.942920884E9 Class A Trunk Road Major 2025-09-20T16:23:09.205Z 7 4 PA 2 East Midlands 2571.21 1597.68 5.535722338E9 Class A Principal road Major 2025-09-20T16:23:09.205Z 33 4 PA 8 Yorkshire and the Humber 2559.104 1590.15 6.365559059E9 Class A Principal road Major 2025-09-20T16:23:09.205Z 50 1 TM 1 South West 304.28 189.07 3.609698716E9 Class A Trunk Motor Major 2025-09-20T16:23:09.205Z 76 3 TA 7 East of England 1131.749 703.24 5.888883553E9 Class A Trunk Road Major 2025-09-20T16:23:09.205Z 8 5 M 2 East Midlands 26712.7 16598.5 7.083362916E9 Class B road Minor 2025-09-20T16:23:09.205Z 28 4 PA 7 East of England 2719.344 1689.72 7.493977513E9 Class A Principal road Major 2025-09-20T16:23:09.205Z 37 3 TA 9 South East 855.597 531.64 5.54362878E9 Class A Trunk Road Major 2025-09-20T16:23:09.205Z 26 1 TM 7 East of England 243.524 151.32 3.92295169E9 Class A Trunk Motor Major 2025-09-20T16:23:09.205Z 16 5 M 4 Wales 28322.4 17598.72 5.286183479E9 Class B road Minor 2025-09-20T16:23:09.205Z 49 5 M 11 North East 14025.9 8715.29 4.664291984E9 Class B road Minor 2025-09-20T16:23:09.205Z 73 4 PA 6 London 1373.23 853.29 7.155061465E9 Class A Principal road Major 2025-09-20T16:23:09.205Z 63 3 TA 4 Wales 1506.139 935.87 3.217899485E9 Class A Trunk Road Major 2025-09-20T16:23:09.205Z 14 3 TA 4 Wales 1509.635 938.04 3.123943528E9 Class A Trunk Road Major 2025-09-20T16:23:09.205Z 55 3 TA 2 East Midlands 1215.788 755.46 5.056721458E9 Class A Trunk Road Major 2025-09-20T16:23:09.205Z 42 3 TA 10 West Midlands 839.786 521.82 3.257861212E9 Class A Trunk Road Major 2025-09-20T16:23:09.205Z 71 1 TM 6 London 66.386 41.25 1.311689053E9 Class A Trunk Motor Major 2025-09-20T16:23:09.205Z 38 4 PA 9 South East 4269.653 2653.04 1.2858678243E10 Class A Principal road Major 2025-09-20T16:23:09.205Z 2 3 TA 1 South West 993.586 617.39 3.48471021E9 Class A Trunk Road Major 2025-09-20T16:23:09.205Z 17 1 TM 5 North West 553.439 343.89 7.184955992E9 Class A Trunk Motor Major 2025-09-20T16:2